In [1]:
import glob, re
import numpy as np
import pandas as pd
from sklearn import *
from datetime import datetime

C:\ProgramData\Anaconda2\lib\site-packages\sklearn\cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
C:\ProgramData\Anaconda2\lib\site-packages\sklearn\grid_search.py:43: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)
C:\ProgramData\Anaconda2\lib\site-packages\sklearn\lda.py:6: DeprecationWarning: lda.LDA has been moved to discriminant_analysis.LinearDiscriminantAnalysis in 0.17 and will be removed in 0.19
  "in 0.17 and will be removed in 0.19", DeprecationWarning)
C:\ProgramData\Anacon

In [2]:
data = {
    'at_tra': pd.read_csv('trainingset/action_train.csv'),
    'of_tra': pd.read_csv('trainingset/orderFuture_train.csv'),
    'oh_tra': pd.read_csv('trainingset/orderHistory_train.csv'),
    'uc_tra': pd.read_csv('trainingset/userComment_train.csv'),
    'up_tra': pd.read_csv('trainingset/userProfile_train.csv'),
    'at_tes': pd.read_csv('test/action_test.csv'),
    'of_tes': pd.read_csv('test/orderFuture_test.csv'),
    'oh_tes': pd.read_csv('test/orderHistory_test.csv'),
    'uc_tes': pd.read_csv('test/userComment_test.csv'),
    'up_tes': pd.read_csv('test/userProfile_test.csv')   
    }

In [3]:
import datetime
def stamp2time(ts):
    return datetime.datetime.fromtimestamp(float(ts)).strftime('%Y-%m-%d %H:%M:%S')

In [4]:
for df in ['at_tra','at_tes']:
    data[df]['actionTime'] = data[df]['actionTime'].apply(lambda x:stamp2time(x))
for df in ['oh_tes','oh_tra']:
    data[df]['orderTime'] = data[df]['orderTime'].apply(lambda x:stamp2time(x))
data['at_tra']['actionTime'] = pd.to_datetime(data['at_tra']['actionTime'])
data['at_tes']['actionTime'] = pd.to_datetime(data['at_tes']['actionTime']) 
data['oh_tra']['orderTime'] = pd.to_datetime(data['oh_tra']['orderTime']) 
data['oh_tes']['orderTime'] = pd.to_datetime(data['oh_tes']['orderTime'])

In [5]:
##get day of week
data['at_tra']['dow'] = data['at_tra']['actionTime'].dt.dayofweek
data['at_tes']['dow'] = data['at_tes']['actionTime'].dt.dayofweek

In [6]:
data['of_tra'] = data['of_tra'].rename(columns={'orderType':'label'})

In [7]:
def get_type_gap(df,args,sets):
    count = pd.value_counts(df.ix[:,args])
    sum_c = count.sum()
    recom = pos = 0
    freq = count.map(lambda x:x/float(sum_c))
    for i in sets:
        if i in freq.index.tolist() and  i==1 :
            recom = freq[i]  
        if i in freq.index.tolist() and i==0 :
            pos = freq[i]  
    if not recom:
        recom = 0
    if not pos:
        pos = 0
    enps = recom-pos
    return enps

In [8]:
type_res = data['oh_tra'].groupby('userid').apply(get_type_gap,args = 'orderType',sets = [0,1])

In [9]:
type_res_df = pd.DataFrame(type_res)
type_res_df = type_res_df.reset_index(drop=True)
type_res_df = type_res_df.rename(columns={0:'pro_gap'}).head(2)

In [10]:
def get_type_count(df,f,args):
    #print df[df.ix[:,args]==f]
    count = len(df[df.ix[:,args]==f])
    return count

In [11]:
##train
tmp_1= data['oh_tra'].groupby('userid').apply(get_type_count,1,args = 'orderType')
tmp_0= data['oh_tra'].groupby('userid').apply(get_type_count,0,args = 'orderType')

In [12]:
##test
tmp_1_tes= data['oh_tes'].groupby('userid').apply(get_type_count,1,args = 'orderType')
tmp_0_tes= data['oh_tes'].groupby('userid').apply(get_type_count,0,args = 'orderType')

In [13]:
##city num
lbl = preprocessing.LabelEncoder()
data['oh_tra']['city'] = lbl.fit_transform(data['oh_tra']['city'])
data['oh_tra']['country'] = lbl.fit_transform(data['oh_tra']['country'])
data['oh_tra']['continent'] = lbl.fit_transform(data['oh_tra']['continent'])
data['oh_tes']['city'] = lbl.fit_transform(data['oh_tes']['city'])
data['oh_tes']['country'] = lbl.fit_transform(data['oh_tes']['country'])
data['oh_tes']['continent'] = lbl.fit_transform(data['oh_tes']['continent'])

In [14]:
def get_city_num(df,args):
    count = len(df.ix[:,args].unique())
    return count
tmp_city_num_tra= data['oh_tra'].groupby('userid').apply(get_city_num,args = 'city')
tmp_city_num_tes= data['oh_tes'].groupby('userid').apply(get_city_num,args = 'city')

In [15]:
tmp_country_num_tra= data['oh_tra'].groupby('userid').apply(get_city_num,args = 'country')
tmp_country_num_tes= data['oh_tes'].groupby('userid').apply(get_city_num,args = 'country')

tmp_continent_num_tra= data['oh_tra'].groupby('userid').apply(get_city_num,args = 'continent')
tmp_continent_num_tes= data['oh_tes'].groupby('userid').apply(get_city_num,args = 'continent')

In [16]:
data['up_tra']['gender'] = lbl.fit_transform(data['up_tra']['gender'])
data['up_tra']['province'] = lbl.fit_transform(data['up_tra']['province'])
data['up_tra']['age'] = lbl.fit_transform(data['up_tra']['age'])

data['up_tes']['gender'] = lbl.fit_transform(data['up_tes']['gender'])
data['up_tes']['province'] = lbl.fit_transform(data['up_tes']['province'])
data['up_tes']['age'] = lbl.fit_transform(data['up_tes']['age'])

C:\ProgramData\Anaconda2\lib\site-packages\numpy\lib\arraysetops.py:200: FutureWarning: numpy not_equal will not check object identity in the future. The comparison did not return the same result as suggested by the identity (`is`)) and will change.
  flag = np.concatenate(([True], aux[1:] != aux[:-1]))


In [17]:
train = pd.merge(data['up_tra'],data['of_tra'], how='left', on=['userid'])
test = pd.merge(data['up_tes'],data['of_tes'], how='left', on=['userid'])

In [18]:
train = pd.merge(train,pd.DataFrame(tmp_1).reset_index().rename(columns={0:'num_jp'}), how='left', on=['userid'])

In [19]:
test = pd.merge(test,pd.DataFrame(tmp_1_tes).reset_index().rename(columns={0:'num_jp'}), how='left', on=['userid'])

In [20]:
train = pd.merge(train,pd.DataFrame(tmp_0).reset_index().rename(columns={0:'num_pt'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_0_tes).reset_index().rename(columns={0:'num_pt'}), how='left', on=['userid'])

In [21]:
train = pd.merge(train,pd.DataFrame(tmp_city_num_tra).reset_index().rename(columns={0:'tmp_city_num'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_city_num_tes).reset_index().rename(columns={0:'tmp_city_num'}), how='left', on=['userid'])

train = pd.merge(train,pd.DataFrame(tmp_country_num_tra).reset_index().rename(columns={0:'tmp_country_num'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_country_num_tes).reset_index().rename(columns={0:'tmp_country_num'}), how='left', on=['userid'])

train = pd.merge(train,pd.DataFrame(tmp_continent_num_tra).reset_index().rename(columns={0:'tmp_continent_num'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_continent_num_tes).reset_index().rename(columns={0:'tmp_continent_num'}), how='left', on=['userid'])

In [23]:
##action features
def get_num_type(df,args):     
    return  len(df.ix[:,args])

In [24]:
tmp_num_type_tra=data['at_tra'].groupby('userid').apply(get_num_type,args = 'actionType')
tmp_num_type_tes=data['at_tes'].groupby('userid').apply(get_num_type,args = 'actionType')

In [25]:
train.head(2)

userid  gender  province  age  label  num_jp  num_pt  \
0  100000000013       2         0    2      0     0.0     2.0   
1  100000000111       0         1    0      0     NaN     NaN   

   tmp_city_num_tra  tmp_country_num_tra  tmp_continent_num_tra  
0               2.0                  2.0                    2.0  
1               NaN                  NaN                    NaN

In [26]:
def get_mean_type(df,args):
    return  df.ix[:,args].mean()
tmp_mean_type_tra=data['at_tra'].groupby('userid').apply(get_mean_type,args = 'actionType')
tmp_mean_type_tes=data['at_tes'].groupby('userid').apply(get_mean_type,args = 'actionType')

In [27]:
def get_median_type(df,args):
    return   df.ix[:,args].median()
tmp_median_type_tra=data['at_tra'].groupby('userid').apply(get_mean_type,args = 'actionType')
tmp_median_type_tes=data['at_tes'].groupby('userid').apply(get_mean_type,args = 'actionType')

In [28]:
train = pd.merge(train,pd.DataFrame(tmp_num_type_tra).reset_index().rename(columns={0:'num_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_num_type_tes).reset_index().rename(columns={0:'num_type'}), how='left', on=['userid'])

train = pd.merge(train,pd.DataFrame(tmp_mean_type_tra).reset_index().rename(columns={0:'tmp_mean_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_mean_type_tes).reset_index().rename(columns={0:'tmp_mean_type'}), how='left', on=['userid'])

train = pd.merge(train,pd.DataFrame(tmp_median_type_tra).reset_index().rename(columns={0:'tmp_median_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_median_type_tes).reset_index().rename(columns={0:'tmp_median_type'}), how='left', on=['userid'])

In [34]:
#train.drop(['tmp_continent_num_tra','tmp_median_type_tra'],axis=1,inplace=True)
#test.head(2)
#test.drop(['tmp_continent_num_tes','tmp_median_type_tes'],axis=1,inplace=True)
test = test.rename(columns={'tmp_city_num_tes':'tmp_city_num_tra','tmp_country_num_tes':'tmp_country_num_tra','tmp_mean_type_tes':'tmp_mean_type_tra'})
test.head(2)

userid  gender  province  age  num_jp  num_pt  tmp_city_num_tra  \
0  100000000371       0         1    0     0.0     1.0               1.0   
1  100000001215       0         0    0     NaN     NaN               NaN   

   tmp_country_num_tra  num_type  tmp_mean_type_tra  
0                  1.0        13           5.307692  
1                  NaN        27           3.444444

In [36]:
def get_action_gap(df,args):
        count = pd.value_counts(df.ix[:,args])
        sum_c = count.sum()
        freq = count.map(lambda x:x/float(sum_c))
        recom = [freq[i] for i in freq.index if i in [1,2,3,4]]
        pos = [freq[i] for i in freq.index if i in [5,6,7,8,9,10]]
        enps = sum(recom)-sum(pos)
        return enps
tmp_gap_type_tra=data['at_tra'].groupby('userid').apply(get_action_gap,args = 'actionType')
tmp_gap_type_tes=data['at_tes'].groupby('userid').apply(get_action_gap,args = 'actionType')

train = pd.merge(train,pd.DataFrame(tmp_gap_type_tra).reset_index().rename(columns={0:'gap_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_gap_type_tes).reset_index().rename(columns={0:'gap_type'}), how='left', on=['userid'])

train.head(2)

userid  gender  province  age  label  num_jp  num_pt  \
0  100000000013       2         0    2      0     0.0     2.0   
1  100000000111       0         1    0      0     NaN     NaN   

   tmp_city_num_tra  tmp_country_num_tra  num_type  tmp_mean_type_tra  \
0               2.0                  2.0       143           3.013986   
1               NaN                  NaN         3           4.000000   

   gap_type  
0  0.188811  
1 -0.333333

In [37]:
train['dow'] = data['at_tra']['dow']
test['dow'] = data['at_tes']['dow']

train['rating'] = data['uc_tra']['rating']
test['rating'] = data['uc_tes']['rating']
train.head(1)

userid  gender  province  age  label  num_jp  num_pt  \
0  100000000013       2         0    2      0     0.0     2.0   

   tmp_city_num_tra  tmp_country_num_tra  num_type  tmp_mean_type_tra  \
0               2.0                  2.0       143           3.013986   

   gap_type  dow  rating  
0  0.188811    0     4.0

In [38]:
def get_max_type(df,args):     
    return  df.ix[:,args].max()
tmp_max_type_tra=data['at_tra'].groupby('userid').apply(get_max_type,args = 'actionType')
tmp_max_type_tes=data['at_tes'].groupby('userid').apply(get_max_type,args = 'actionType')
 
train = pd.merge(train,pd.DataFrame(tmp_max_type_tra).reset_index().rename(columns={0:'last_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_max_type_tes).reset_index().rename(columns={0:'last_type'}), how='left', on=['userid'])

train.head(1)

userid  gender  province  age  label  num_jp  num_pt  \
0  100000000013       2         0    2      0     0.0     2.0   

   tmp_city_num_tra  tmp_country_num_tra  num_type  tmp_mean_type_tra  \
0               2.0                  2.0       143           3.013986   

   gap_type  dow  rating  last_type  
0  0.188811    0     4.0          9

In [39]:
def get_min_type(df,args):     
    return  df.ix[:,args].min()
tmp_min_type_tra=data['at_tra'].groupby('userid').apply(get_min_type,args = 'actionType')
tmp_min_type_tes=data['at_tes'].groupby('userid').apply(get_min_type,args = 'actionType')
 
train = pd.merge(train,pd.DataFrame(tmp_min_type_tra).reset_index().rename(columns={0:'first_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_min_type_tes).reset_index().rename(columns={0:'first_type'}), how='left', on=['userid'])

#train.head(1)

In [46]:
def get_last_2th_type(df,args):
    s = list(df.ix[:,args].unique())
    s.sort()
    print s
    return s[-2] if len(s)>1 else s[-1]
tmp_last_2th_type_tra=data['at_tra'].groupby('userid').apply(get_last_2th_type,args = 'actionType')
tmp_last_2th_type_tes=data['at_tes'].groupby('userid').apply(get_last_2th_type,args = 'actionType')
 
train = pd.merge(train,pd.DataFrame(tmp_last_2th_type_tra).reset_index().rename(columns={0:'last_2th_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_last_2th_type_tes).reset_index().rename(columns={0:'last_2th_type'}), how='left', on=['userid'])
test.head(2)

[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 5, 6]
[1, 5, 7]
[1, 2, 3, 4, 5, 6]
[1, 2, 3, 4, 5, 6, 7]
[1, 3, 5, 6, 7, 8, 9]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 5, 6, 8, 9]
[1, 5, 6, 8, 9]
[1, 3, 5, 6, 8]
[1, 5, 6]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 5, 6, 8, 9]
[1, 5]
[1, 2, 3, 4, 5, 6, 7]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 5]
[1, 5, 6, 8]
[1, 5, 6, 7, 8, 9]
[1, 5, 6, 7, 8, 9]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 5, 6]
[1, 2, 5, 6, 7]
[1, 5, 6, 8, 9]
[1, 5]
[1, 2, 5, 6, 7, 8, 9]
[1, 5, 6]
[1, 5, 6]
[1]
[1, 5, 6]
[1, 5, 6, 8, 9]
[1, 2, 4, 5, 6, 7]
[1, 2, 4, 5, 6, 8, 9]
[1, 5]
[1, 3, 4, 5, 7]
[1, 5, 6]
[1, 2, 4, 5, 6]
[1, 5, 6, 7, 8, 9]
[1, 2, 3, 4, 5, 6]
[1, 5]
[5]
[1, 3, 5, 6, 7]
[2, 5]
[1, 2, 3, 5, 6, 7]
[1, 5, 6]
[1, 5, 6, 8, 9]
[1, 2, 3, 4, 5, 6, 8, 9]
[1, 2, 3, 4, 5, 6, 8]
[1, 5, 6, 8, 9]
[1]
[1, 5, 6]
[1, 5, 6, 7, 9]
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[1, 4, 5, 6, 7]
[1, 5, 7]
[1, 5, 6, 8, 9]
[1, 5]
[1, 2, 3, 4, 5, 6, 9]
[1]
[1, 2, 5

userid  gender  province  age  num_jp  num_pt  tmp_city_num_tra  \
0  100000000371       0         1    0     0.0     1.0               1.0   
1  100000001215       0         0    0     NaN     NaN               NaN   

   tmp_country_num_tra  num_type  tmp_mean_type_tra  gap_type  dow  rating  \
0                  1.0        13           5.307692 -0.846154    2     5.0   
1                  NaN        27           3.444444 -0.185185    2     5.0   

   last_type  first_type  last_2th_type  
0          7           1              6  
1          6           1              5

In [48]:
def get_last_3th_type(df,args):
    s = list(df.ix[:,args].unique())
    s.sort()
    return s[-3] if len(s)>2 else s[-1]
tmp_last_3th_type_tra=data['at_tra'].groupby('userid').apply(get_last_3th_type,args = 'actionType')
tmp_last_3th_type_tes=data['at_tes'].groupby('userid').apply(get_last_3th_type,args = 'actionType')
 
train = pd.merge(train,pd.DataFrame(tmp_last_3th_type_tra).reset_index().rename(columns={0:'last_3th_type'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_last_3th_type_tes).reset_index().rename(columns={0:'last_3th_type'}), how='left', on=['userid'])

In [57]:
def time_gap_mean(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    return d.mean()
tmp_time_gap_mean_tra=data['at_tra'].groupby('userid').apply(time_gap_mean,args = 'actionTime')
tmp_time_gap_mean_tes=data['at_tes'].groupby('userid').apply(time_gap_mean,args = 'actionTime')
 
train = pd.merge(train,pd.DataFrame(tmp_time_gap_mean_tra).reset_index().rename(columns={0:'time_gap_mean'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_time_gap_mean_tes).reset_index().rename(columns={0:'time_gap_mean'}), how='left', on=['userid'])

test.head(2)

userid  gender  province  age  num_jp  num_pt  tmp_city_num_tra  \
0  100000000371       0         1    0     0.0     1.0               1.0   
1  100000001215       0         0    0     NaN     NaN               NaN   

   tmp_country_num_tra  num_type  tmp_mean_type_tra  gap_type  dow  rating  \
0                  1.0        13           5.307692 -0.846154    2     5.0   
1                  NaN        27           3.444444 -0.185185    2     5.0   

   last_type  first_type  last_2th_type  last_3th_type  time_gap_mean_x  \
0          7           1              6              5              0.0   
1          6           1              5              1              0.0   

         time_gap_mean_y  
0 0 days 00:08:47.750000  
1 5 days 08:13:54.192307

In [60]:
#train['time_gap_mean'] = train['time_gap_mean_y'].astype('timedelta64[s]')
#test['time_gap_mean'] = test['time_gap_mean_y'].astype('timedelta64[s]')
#train.drop(['time_gap_mean_x','time_gap_mean_y'],axis=1,inplace=True)
#test.drop(['time_gap_mean_x','time_gap_mean_y'],axis=1,inplace=True)

In [61]:
#test.head(2)

userid  gender  province  age  num_jp  num_pt  tmp_city_num_tra  \
0  100000000371       0         1    0     0.0     1.0               1.0   
1  100000001215       0         0    0     NaN     NaN               NaN   

   tmp_country_num_tra  num_type  tmp_mean_type_tra  gap_type  dow  rating  \
0                  1.0        13           5.307692 -0.846154    2     5.0   
1                  NaN        27           3.444444 -0.185185    2     5.0   

   last_type  first_type  last_2th_type  last_3th_type  time_gap_mean  
0          7           1              6              5          527.0  
1          6           1              5              1       461634.0

In [64]:
def time_gap_std(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    return d.std()
tmp_time_gap_std_tra=data['at_tra'].groupby('userid').apply(time_gap_std,args = 'actionTime').astype('timedelta64[s]')
tmp_time_gap_std_tes=data['at_tes'].groupby('userid').apply(time_gap_std,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_time_gap_std_tra).reset_index().rename(columns={0:'time_gap_std'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_time_gap_std_tes).reset_index().rename(columns={0:'time_gap_std'}), how='left', on=['userid'])

test.head(2)

userid  gender  province  age  num_jp  num_pt  tmp_city_num_tra  \
0  100000000371       0         1    0     0.0     1.0               1.0   
1  100000001215       0         0    0     NaN     NaN               NaN   

   tmp_country_num_tra  num_type  tmp_mean_type_tra  gap_type  dow  rating  \
0                  1.0        13           5.307692 -0.846154    2     5.0   
1                  NaN        27           3.444444 -0.185185    2     5.0   

   last_type  first_type  last_2th_type  last_3th_type  time_gap_mean  \
0          7           1              6              5          527.0   
1          6           1              5              1       461634.0   

   time_gap_quantile  time_gap_std  
0              174.0        1263.0  
1           244765.0     1090672.0

In [63]:
def time_gap_quantile(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    return d.quantile(0.75)
tmp_time_gap_quantile_tra=data['at_tra'].groupby('userid').apply(time_gap_quantile,args = 'actionTime').astype('timedelta64[s]')
tmp_time_gap_quantile_tes=data['at_tes'].groupby('userid').apply(time_gap_quantile,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_time_gap_quantile_tra).reset_index().rename(columns={0:'time_gap_quantile'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_time_gap_quantile_tes).reset_index().rename(columns={0:'time_gap_quantile'}), how='left', on=['userid'])

test.head(2)

userid  gender  province  age  num_jp  num_pt  tmp_city_num_tra  \
0  100000000371       0         1    0     0.0     1.0               1.0   
1  100000001215       0         0    0     NaN     NaN               NaN   

   tmp_country_num_tra  num_type  tmp_mean_type_tra  gap_type  dow  rating  \
0                  1.0        13           5.307692 -0.846154    2     5.0   
1                  NaN        27           3.444444 -0.185185    2     5.0   

   last_type  first_type  last_2th_type  last_3th_type  time_gap_mean  \
0          7           1              6              5          527.0   
1          6           1              5              1       461634.0   

   time_gap_quantile  
0              174.0  
1           244765.0

In [66]:
def min_time_gap(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    return d.min()
tmp_min_time_gap_tra=data['at_tra'].groupby('userid').apply(min_time_gap,args = 'actionTime').astype('timedelta64[s]')
tmp_min_time_gap_tes=data['at_tes'].groupby('userid').apply(min_time_gap,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_min_time_gap_tra).reset_index().rename(columns={0:'min_time_gap'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_min_time_gap_tes).reset_index().rename(columns={0:'min_time_gap'}), how='left', on=['userid'])

test.head(2)

userid  gender  province  age  num_jp  num_pt  tmp_city_num_tra  \
0  100000000371       0         1    0     0.0     1.0               1.0   
1  100000001215       0         0    0     NaN     NaN               NaN   

   tmp_country_num_tra  num_type  tmp_mean_type_tra      ...       dow  \
0                  1.0        13           5.307692      ...         2   
1                  NaN        27           3.444444      ...         2   

   rating  last_type  first_type  last_2th_type  last_3th_type  time_gap_mean  \
0     5.0          7           1              6              5          527.0   
1     5.0          6           1              5              1       461634.0   

   time_gap_quantile  time_gap_std  min_time_gap  
0              174.0        1263.0           3.0  
1           244765.0     1090672.0           2.0  

[2 rows x 21 columns]

# write to csv

In [68]:
train.to_csv('train_part1.csv')
test.to_csv('test_part1.csv')

In [ ]:
def last_time_gap(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    #print d
    return d.iloc[-1] if len(d)>1 else 0
tmp_last_time_gap_tra=data['at_tra'].groupby('userid').apply(last_time_gap,args = 'actionTime').astype('timedelta64[s]')
tmp_last_time_gap_tes=data['at_tes'].groupby('userid').apply(last_time_gap,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_last_time_gap_tra).reset_index().rename(columns={0:'last_time_gap'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_last_time_gap_tes).reset_index().rename(columns={0:'last_time_gap'}), how='left', on=['userid'])

test.head(2)

1      0 days 00:00:10
2      0 days 00:01:51
3      0 days 00:00:37
4      0 days 00:00:25
5      0 days 00:00:05
6      0 days 00:00:31
7      0 days 00:00:18
8      0 days 00:19:46
9      0 days 00:00:18
10     2 days 01:22:20
11     1 days 00:10:34
12     0 days 00:00:24
13     1 days 01:08:01
14     4 days 16:24:19
15     1 days 08:24:33
16     0 days 00:00:13
17    75 days 15:25:31
18     0 days 00:02:16
19     0 days 00:00:34
20     0 days 00:37:37
21     0 days 15:29:55
22     0 days 10:59:21
23     0 days 00:08:48
24     0 days 00:00:08
25     0 days 00:00:02
26     0 days 00:00:39
27     0 days 00:00:04
28     0 days 07:14:24
29     0 days 00:48:26
30     0 days 00:01:21
            ...       
113   76 days 22:54:49
114    0 days 09:15:34
115    0 days 00:01:04
116    0 days 00:01:18
117   70 days 21:03:27
118    0 days 00:09:19
119    0 days 00:01:37
120    0 days 00:00:04
121    0 days 00:00:11
122    0 days 04:32:32
123    0 days 00:11:49
124    0 days 00:29:54
125    0 da

In [ ]:
def last_2_time_gap(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    #print d
    return d.iloc[-2] if len(d)>2 else 0
tmp_last_2_time_gap_tra=data['at_tra'].groupby('userid').apply(last_2_time_gap,args = 'actionTime').astype('timedelta64[s]')
tmp_last_2_time_gap_tes=data['at_tes'].groupby('userid').apply(last_2_time_gap,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_last_2_time_gap_tra).reset_index().rename(columns={0:'last_2_time_gap'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_last_2_time_gap_tes).reset_index().rename(columns={0:'last_2_time_gap'}), how='left', on=['userid'])

test.head(2)

In [ ]:
def last_3_time_gap(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    #print d
    return d.iloc[-3] if len(d)>3 else 0
tmp_last_3_time_gap_tra=data['at_tra'].groupby('userid').apply(last_3_time_gap,args = 'actionTime').astype('timedelta64[s]')
tmp_last_3_time_gap_tes=data['at_tes'].groupby('userid').apply(last_3_time_gap,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_last_3_time_gap_tra).reset_index().rename(columns={0:'last_3_time_gap'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_last_3_time_gap_tes).reset_index().rename(columns={0:'last_3_time_gap'}), how='left', on=['userid'])

test.head(2)

In [ ]:
def last_4_time_gap(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    #print d
    return d.iloc[-4] if len(d)>2 else 0
tmp_last_4_time_gap_tra=data['at_tra'].groupby('userid').apply(last_4_time_gap,args = 'actionTime').astype('timedelta64[s]')
tmp_last_4_time_gap_tes=data['at_tes'].groupby('userid').apply(last_4_time_gap,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_last_4_time_gap_tra).reset_index().rename(columns={0:'last_4_time_gap'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_last_4_time_gap_tes).reset_index().rename(columns={0:'last_4_time_gap'}), how='left', on=['userid'])

test.head(2)

In [ ]:
def first_time_gap(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    #print d
    return d.iloc[0] if len(d)>0 else 0
tmp_first_time_gap_tra=data['at_tra'].groupby('userid').apply(first_time_gap,args = 'actionTime').astype('timedelta64[s]')
tmp_first_time_gap_tes=data['at_tes'].groupby('userid').apply(first_time_gap,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_first_time_gap_tra).reset_index().rename(columns={0:'first_time_gap'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_first_time_gap_tes).reset_index().rename(columns={0:'first_time_gap'}), how='left', on=['userid'])

test.head(2)

In [ ]:
def first_time_gap(df,args):
    c = df.ix[:,args]
    d = (c - c.shift()).dropna()
    #print d
    return d.iloc[0] if len(d)>0 else 0
tmp_first_time_gap_tra=data['at_tra'].groupby('userid').apply(first_time_gap,args = 'actionTime').astype('timedelta64[s]')
tmp_first_time_gap_tes=data['at_tes'].groupby('userid').apply(first_time_gap,args = 'actionTime').astype('timedelta64[s]')
 
train = pd.merge(train,pd.DataFrame(tmp_first_time_gap_tra).reset_index().rename(columns={0:'first_time_gap'}), how='left', on=['userid'])
test = pd.merge(test,pd.DataFrame(tmp_first_time_gap_tes).reset_index().rename(columns={0:'first_time_gap'}), how='left', on=['userid'])

test.head(2)

In [ ]:
train.fillna(0,inplace = True)
test.fillna(0,inplace = True)

In [ ]:
test.drop(test.columns[4],axis=1,inplace=True)

In [ ]:
test = test.rename(columns={'num_pt_y':'num_pt','num_jp_y':'num_jp'})

# train

In [106]:
col = [c for c in train if c not in ['userid','label']]

def RMSLE(y, pred):
    return metrics.mean_squared_error(y, pred)**0.5
    
model1 = ensemble.GradientBoostingRegressor(learning_rate=0.2, random_state=3, n_estimators=200, subsample=0.8, 
                      max_depth =10)
model2 = neighbors.KNeighborsRegressor(n_jobs=-1, n_neighbors=4)
#model3 = XGBRegressor(learning_rate=0.2, random_state=3, n_estimators=200, subsample=0.8, 
#                      colsample_bytree=0.8, max_depth =10)

model1.fit(train[col], train['label'].values )
model2.fit(train[col],  train['label'].values )
#model3.fit(train[col], np.log1p(train['visitors'].values))

preds1 = model1.predict(train[col])
preds2 = model2.predict(train[col])
#preds3 = model3.predict(train[col])

print('RMSE GradientBoostingRegressor: ', RMSLE( train['label'].values , preds1))
print('RMSE KNeighborsRegressor: ', RMSLE( train['label'].values , preds2))
#print('RMSE XGBRegressor: ', RMSLE(np.log1p(train['visitors'].values), preds3))


('RMSE GradientBoostingRegressor: ', 0.14689688016979027)
('RMSE KNeighborsRegressor: ', 0.30213717620945452)


In [109]:
test = test.rename(columns={'tmp_mean_type_tes':'tmp_mean_type_tra','tmp_median_type_tes':'tmp_median_type_tra'})
#test = test.rename(columns={'tmp_city_num_tes':'tmp_city_num_tra','tmp_country_num_tes':'tmp_country_num_tra','tmp_continent_num_tes':'tmp_continent_num_tra'})

In [110]:
preds1 = model1.predict(test[col])
preds2 = model2.predict(test[col])
#preds3 = model3.predict(test[col])

In [111]:
submit = pd.DataFrame(columns = ['userid','orderType'])

In [113]:
##submit
submit['orderType'] = 0.75*preds1+0.25*preds2 
submit['userid']= test['userid']
#submission = pd.read_csv('submit.csv') 
submit.to_csv('submission.csv', index=False)

In [114]:
submission.head(2)

userid  orderType
0  100000000371        0.5
1  100000001215        0.5